In [1]:
from google.transit import gtfs_realtime_pb2
import requests
from collections import defaultdict
import time
from datetime import datetime
import pandas as pd
from copy import deepcopy
import schedule
from ST_DBSCAN.stdbscan import STDBSCAN
import sys
from tqdm import tqdm
import folium
from folium.plugins import MarkerCluster
from folium.plugins import Search
from collections import Counter
route_dict = {}
# read entity data from protobuffer
def get_entity_data(entity):
    vehicle_id = entity.vehicle.vehicle.id
    vehicle_lat = entity.vehicle.position.latitude
    vehicle_lon = entity.vehicle.position.longitude
    vehicle_route_id = str(int(float(entity.vehicle.trip.route_id)))
    vehicle_timestamp = entity.vehicle.timestamp
    return vehicle_id, vehicle_lat, vehicle_lon, vehicle_route_id, vehicle_timestamp


def read_feed():
    # print(OTD_RT_URL)
    feed = gtfs_realtime_pb2.FeedMessage()
    try:
        response = requests.get(OTD_RT_URL)
        feed.ParseFromString(response.content)
        # print("Feed at " + str(datetime.datetime.now()))
    except TimeoutError:
        print("URL Timeout")
    except requests.exceptions.ConnectionError:
        print('Max retries exceeded')
    return feed

def read_routes():
    global route_dict
    routes = open('routes.txt','r')
    routes_data = routes.readlines()
    routes.close()
    
    for i in routes_data:
        i = i.split(',')
        route_dict[i[3]] = i[1]
    
    return route_dict

def run_db_scan(df, spatial_threshold=50, temporal_threshold=20, min_neighbors=12):
    if len(df) == 0:
        print(df)
    st_dbscan = STDBSCAN(col_lat='lat', col_lon='lng',
                         col_time='timestamp', spatial_threshold=spatial_threshold,
                         temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)
    df = st_dbscan.projection(df, p1_str='epsg:4326', p2_str='epsg:32635')
    result_t600 = st_dbscan.run(df)
    return result_t600


def save_to_dict():
    global remove_element_flag
    feed = read_feed()
    # print(feed)
    if time.time() - process_start_timestamp >= 1200:
        remove_element_flag = True
    for entity in feed.entity:
        # print(entity)
        vehicle_id, vehicle_lat, vehicle_lon, vehicle_route_id, vehicle_timestamp = get_entity_data(entity)
        if pb_data_dict.get(vehicle_id):
            if not (datetime.fromtimestamp(int(vehicle_timestamp)) in pb_data_dict[vehicle_id]['timestamp'] and vehicle_lat in pb_data_dict[vehicle_id]['lat'] and vehicle_lon in pb_data_dict[vehicle_id]['lng'] and vehicle_route_id in pb_data_dict[vehicle_id]['route_id']):
                pb_data_dict[vehicle_id]['lat'].append(vehicle_lat)
                pb_data_dict[vehicle_id]['lng'].append(vehicle_lon)
                pb_data_dict[vehicle_id]['timestamp'].append(datetime.fromtimestamp(int(vehicle_timestamp)))
                pb_data_dict[vehicle_id]['route_id'].append(vehicle_route_id)
                if remove_element_flag:
                    print('deleted for ', vehicle_id)
                    if len(pb_data_dict[vehicle_id]['lat']) <= 1:
                        del pb_data_dict[vehicle_id]
                    else:
                        pb_data_dict[vehicle_id]['lat'].pop(0)
                        pb_data_dict[vehicle_id]['lng'].pop(0)
                        pb_data_dict[vehicle_id]['timestamp'].pop(0)
                        pb_data_dict[vehicle_id]['route_id'].pop(0)
        else:
            vehicle_data_dict = defaultdict(list)
            vehicle_data_dict['lat'].append(vehicle_lat)
            vehicle_data_dict['lng'].append(vehicle_lon)
            vehicle_data_dict['timestamp'].append(datetime.fromtimestamp(int(vehicle_timestamp)))
            vehicle_data_dict['route_id'].append(vehicle_route_id)
            
            pb_data_dict[vehicle_id] = vehicle_data_dict
    # print(pb_data_dict)


def calculate_centroid(list_of_coordinates):
    return sum(list_of_coordinates)/len(list_of_coordinates)


def cluster_json_data(bus, pb_data_dict):
    global route_dict
    lat_list = pb_data_dict[bus]['lat']
    lng_list = pb_data_dict[bus]['lng']

    lat_centroid = calculate_centroid(lat_list)
    lng_centroid = calculate_centroid(lng_list)

#     timestamp = int(time.time())
    timestamp = pb_data_dict[bus]['timestamp'][-1]
    route_id = pb_data_dict[bus]['route_id'][0]
    route_dir = route_dict[route_id]

    bus_data = {'vehicle_id': bus, 'lat': lat_centroid, 'lng': lng_centroid, 'timestamp': timestamp, 'route_id' : route_id ,'route_direction':route_dir}

    return bus_data


def chk_cluster():
    global clustered_buses_list
    # production
    # spatial_threshold = 10
    # temporal_threshold = 900
    # min_neighbors = 90

    # testing (less time gap)
    spatial_threshold = 10
    temporal_threshold = 300
    min_neighbors = 30
    clustered_buses_data = []
    start = time.time()
    temp_list = list()
    print(len(pb_data_dict), "dict")
    for bus in tqdm(pb_data_dict.keys()):
        bus_data_df = pd.DataFrame.from_dict(pb_data_dict[bus])
#         return bus_data_df
        if len(bus_data_df) != 0:
            clustered_df = run_db_scan(deepcopy(bus_data_df), spatial_threshold=spatial_threshold,
                                       temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)
#             return clustered_df
            bus_data_df['cluster'] = clustered_df['cluster']
            # unique_clusters = chk_if_cluster_close_to_depot(bus_data_df)
            unique_clusters = pd.unique(bus_data_df.cluster)
#             return bus_data_df
            if len(unique_clusters) > 1:
                bus_data = cluster_json_data(bus,pb_data_dict)
#                 print('cluster detected for ',bus,bus_data)
#                 print(pb_data_dict[bus])
                clustered_buses_data.append(bus_data)
                temp_list.append(bus)
            else:
#                 print('no cluster detected for ', bus)
                pass
    clustered_buses_list = temp_list
#     print(clustered_buses_list)
#     print(time.time() - start)
    return clustered_buses_data

def plot_map():
    prob_buses = chk_cluster()
    start_lat = 28.617453756786528
    start_lon = 77.20423389616467

    m=folium.Map(location=[start_lat,start_lon],tiles='Open Street Map', zoom_start=10)
    for i in prob_buses:
    #     print(i)
        lat = i['lat']
        lng = i['lng']
        folium.Circle(
          location=[lat, lng],
          popup=i['vehicle_id'],
          color='crimson',
          fill=True,
          fill_color='crimson'
       ).add_to(m)
    m.save('map1.html')
    

if __name__ == '__main__':
    OTD_API_KEY = 'X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u'
    OTD_RT_URL = f'https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key={OTD_API_KEY}'
    print('OTD API URL', OTD_RT_URL)
    read_routes()
    pb_data_dict = {}
    clustered_buses_list = list()
    remove_element_flag = False
    process_start_timestamp = time.time()
    schedule.every(10).seconds.do(save_to_dict)
#     schedule.every(180).seconds.do(chk_cluster)
#     schedule.every(600).seconds.do(plot_map)
    counter = 0
    while counter < 600:
        schedule.run_pending()
        time.sleep(1)
        counter += 1
        print(counter)




OTD API URL https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key=X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
2

In [2]:
# OTD_API_KEY = 'X5xn9r7RQ8j2xAQgIMWA9p3BlJMMy28u'
# OTD_RT_URL = f'https://otd.delhi.gov.in/api/realtime/VehiclePositions.pb?key={OTD_API_KEY}'
# print('OTD API URL', OTD_RT_URL)

# pb_data_dict = {}
# clustered_buses_list = list()
# remove_element_flag = False
# process_start_timestamp = time.time()

In [6]:
! pip install pyproj

  Using cached pyproj-3.3.0-cp38-cp38-win_amd64.whl (6.3 MB)


In [2]:
# save_to_dict()

In [3]:
pb_data_dict

{'DL1PD5111': defaultdict(list,
             {'lat': [28.509361267089844,
               28.509401321411133,
               28.509414672851562,
               28.510356903076172,
               28.51105499267578,
               28.51133918762207,
               28.51149559020996,
               28.51171875,
               28.513050079345703,
               28.51375961303711,
               28.514312744140625,
               28.51442527770996,
               28.515989303588867,
               28.51696014404297,
               28.518831253051758,
               28.519805908203125,
               28.52072525024414,
               28.521480560302734,
               28.522573471069336,
               28.522972106933594,
               28.524059295654297,
               28.524097442626953,
               28.524206161499023,
               28.524280548095703,
               28.524288177490234,
               28.524372100830078,
               28.52456283569336,
               28.5249080657959

In [4]:
prob_buses = chk_cluster()

  0%|▎                                                                                | 7/2020 [00:00<00:31, 63.81it/s]

2020 dict


100%|██████████████████████████████████████████████████████████████████████████████| 2020/2020 [00:29<00:00, 67.82it/s]


In [5]:
len(prob_buses)

87

In [6]:
prob_buses


[{'vehicle_id': 'DL1PD5098',
  'lat': 28.666037877400715,
  'lng': 77.22218146690956,
  'timestamp': datetime.datetime(2022, 4, 16, 15, 16, 2),
  'route_id': '467',
  'route_direction': '120DOWN'},
 {'vehicle_id': 'DL1PD5369',
  'lat': 28.652821901109483,
  'lng': 77.10846811930338,
  'timestamp': datetime.datetime(2022, 4, 16, 15, 15, 56),
  'route_id': '539',
  'route_direction': '998UP'},
 {'vehicle_id': 'DL1PD3250',
  'lat': 28.626692913948222,
  'lng': 77.11115784340717,
  'timestamp': datetime.datetime(2022, 4, 16, 15, 15, 57),
  'route_id': '733',
  'route_direction': '73UP'},
 {'vehicle_id': 'DL1PC6505',
  'lat': 28.725428581237793,
  'lng': 77.18219108581543,
  'timestamp': datetime.datetime(2022, 4, 16, 15, 15, 51),
  'route_id': '1145',
  'route_direction': '7LNKSTLUP'},
 {'vehicle_id': 'DL1PD4891',
  'lat': 28.66038586876609,
  'lng': 77.2256535616788,
  'timestamp': datetime.datetime(2022, 4, 16, 15, 16, 6),
  'route_id': '755',
  'route_direction': '136DOWN'},
 {'vehicle_

In [7]:
cl1_bus_df = pd.DataFrame.from_dict(prob_buses)

In [8]:
cl1_bus_df['timestamp'] = pd.to_datetime(cl1_bus_df['timestamp'], unit = 's')

In [9]:
cl1_bus_df

vehicle_id        lat        lng           timestamp route_id  \
0   DL1PD5098  28.666038  77.222181 2022-04-16 15:16:02      467   
1   DL1PD5369  28.652822  77.108468 2022-04-16 15:15:56      539   
2   DL1PD3250  28.626693  77.111158 2022-04-16 15:15:57      733   
3   DL1PC6505  28.725429  77.182191 2022-04-16 15:15:51     1145   
4   DL1PD4891  28.660386  77.225654 2022-04-16 15:16:06      755   
..        ...        ...        ...                 ...      ...   
82  DL1PC6580  28.803238  77.042099 2022-04-16 15:15:59     1042   
83  DL1PD0107  28.625922  77.065421 2022-04-16 15:15:49      549   
84  DL1PD0650  28.625534  77.066001 2022-04-16 15:15:49      549   
85  DL1PD0865  28.590570  77.233180 2022-04-16 15:15:49      103   
86  DL1PC4196  28.716887  77.101738 2022-04-16 15:16:00     1180   

   route_direction  
0          120DOWN  
1            998UP  
2             73UP  
3        7LNKSTLUP  
4          136DOWN  
..             ...  
82      972EXTDOWN  
83           883UP  
84           883UP  
85         588DOWN  
86       990CLDOWN  

[87 rows x 6 columns]

In [ ]:
spatial_threshold = 300
temporal_threshold = 600
min_neighbors = 3
clustered_df2 = run_db_scan(deepcopy(cl1_bus_df), spatial_threshold=spatial_threshold,
                                       temporal_threshold=temporal_threshold, min_neighbors=min_neighbors)

In [ ]:
Counter(clustered_df2.cluster)

In [ ]:
clustered_df2